# Amsterdam AirBNB Price Analysis

#### Notebook Contents
1. [Introduction](#intro)
1. [Research Questions](#researchquestions)
1. [Dataset](#dataset)
2. [Data Cleaning](#cleaning)
3. [Feature Engineering](#featureengineering)
4. [Data Analysis](#dataanalysis)
5. [Data Visualizations](#datavisualization)
6. [Insights](#Insichts)

### 1. Introduction
In my free time I conducted the following hobby project analyzing a dataset of Airbnb Listings in Amsterdam. I employed various techniques in data manipulation, visualization, statistical analysis, and domain knowledge to uncover meaningful patterns and trends. I was most interested in identifying variables correlated to the price of a listing, looking to describe and derive insight about AirBnb prices in Amsterdam. To that end the project will be of interest to AirBnB guests and hosts alike wanting to learn more about the lodging possibilities in Amsterdam. 

Libraries used: Pandas, Numpy, Pandas Profiling Geopandas, Statsmodels.api, Scipy.stats, Regex (re), Requests, JSON, Folium, Branca.colormap (cm), Shapely.geometry (Point), Geopy.distance (geodesic), Datetime (datetime as dt), Plotly.graph_objs (go), Plotly.express (px), Plotly.subplots (make_subplots) 

In [414]:
import pandas as pd
import numpy as np
import pandas_profiling
import geopandas as gpd
import statsmodels.api as sm
from statsmodels.formula.api import ols
import scipy.stats as stats
from statsmodels.stats.multicomp import pairwise_tukeyhsd
import regex as re

import requests
import json

import folium
import branca.colormap as cm
from shapely.geometry import Point
from shapely.geometry.polygon import Polygon
from geopy.distance import geodesic
from datetime import datetime as dt


import plotly.graph_objs as go
import plotly.express as px
from plotly.subplots import make_subplots


### 2. Research Questions

Mind you the purpose of this project is to practice data analysis and visualization techniques, not to create Machine Learning models. For this reason certain decisions in the data cleaning process might defer from techniques used to prepare data for Machine Learning. This will therefore affect decisions with regard to outliers, missing values and which columns may or not may be of intrest. The following questions are meant to guide the analysis: 

- **What are the correlations with AirBnB prices and the other features of the dataset? How much variance in price can be explained by other features?**
- **Which neighborhoods have significantly different prices amongst each other?**
- **Is there a correlation between AirBnB prices and housing values by neighborhood?**
- **What is the impact of reviews on the price of an AirBnB listings?**
- **What are the most important features in predicting AirBnB prices?**


### 3. Dataset

'Airbnb.csv' file downloaded from Kaggle through the following [link](#https://www.kaggle.com/datasets/thedevastator/exploring-amsterdam-airbnb-hosts-locations-ratin?select=airbnb.csv). The dataset includes the following 34 features with 7833 entries:
-	**_'index'_**: Unique identifier for each observation in the dataset.
-	**_'host_id'_**: Identifier for each Airbnb host.
-	**_'host_name'_**: Name of the Airbnb host.
-	**_'host_since_year'_**: Year the host joined Airbnb.
-	**_'host_since_anniversary'_**: Month and Day the host joined Airbnb (anniversary).
-	**_'id'_**: Unique identifier for each Airbnb listing.
-	**_'neighbourhood_cleansed'_**: Specific neighborhood in Amsterdam where the listing is located.
-	**_'city'_**: City where the listing is located (typically Amsterdam).
-	**_'state'_**: Region of The Netherlands where the listing is located (typically Noord-Holland)
-	**_'zipcode'_**: Postal code of the listing's location.
-	**_'country'_**: Country where the listing is located (The Netherlands).
-	**_'latitude'_** and **_'longitude'_**: Geographic coordinates of the listing's location.
-	**_'property_type'_**: Type of property being listed (e.g., apartment, house, villa).
-	**_'room_type'_**: Type of room or space available for guests.
-	**_'accommodates'_**: Maximum number of guests the listing can accommodate.
-	**_'bathrooms'_**: Number of bathrooms in the listing.
-	**_'bedrooms'_**: Number of bedrooms in the listing.
-	**_'beds'_**: Number of beds in the listing.
-	**_'bed_type'_**: Type of bed provided in the listing.
-	**_'price'_**: Rental price per night for the listing.
-	**_'guests_included'_**: Number of guests included in the base rental price.
-	**_'extra_people'_**: Additional charge for each additional guest.
-	**_'minimum_nights'_**: Minimum number of nights guests must book.
-	**_'host_response_time'_**: Response time of the host to guest inquiries as a string (eg. within 30 minutes, within one hour, etc)
-	**_'host_response_rate'_**: Rate of guest inquiries responded to by the host.
-	**_'number_of_reviews'_**: Total number of reviews received for the listing.
-	**_'review_scores_rating'_**: Overall rating score given by guests in reviews.
-	**_'review_scores_accuracy'_**: Rating score for accuracy in guest reviews.
-	**_'review_scores_cleanliness'_**: Rating score for cleanliness in guest reviews.
-	**_'review_scores_checkin'_**: Rating score for check-in experience in guest reviews.
-	**_'review_scores_communication'_**: Rating score for communication in guest reviews.
-	**_'review_scores_location'_**: Rating score for location in guest reviews.
-	**_'review_scores_value'_**: Rating score for value in guest reviews.

Additional data was downloaded from Amsterdam’s municipality open data repository. Specifically data with regard to housing values from 2021 in different neighborhoods of the city. This data was ingested using requests as a GeoJSON file and processed using geopandas. The following [Link](#https://maps.amsterdam.nl/open_geodata/) was used.




##### Load Data

In [415]:
data = pd.read_csv('Data/airbnb.csv')
data.head(3)

index  host_id host_name  host_since_year host_since_anniversary      id  \
0      0     1662     Chloe             2008                   8/11  304958   
1      1     3159    Daniel             2008                   9/24    2818   
2      2     3718    Britta             2008                  10/19  103026   

                   neighbourhood_cleansed       city          state zipcode  \
0                              Westerpark  Amsterdam  North Holland    1053   
1  Oostelijk Havengebied - Indische Buurt  Amsterdam  North Holland     NaN   
2                  De Baarsjes - Oud-West  Amsterdam  Noord-Holland    1053   

   ...  host_response_time  host_response_rate  number_of_reviews  \
0  ...        within a day                 0.8                 11   
1  ...      within an hour                 1.0                108   
2  ...  within a few hours                 1.0                 15   

  review_scores_rating review_scores_accuracy  review_scores_cleanliness  \
0                 98.0                   10.0                       10.0   
1                 97.0                   10.0                       10.0   
2                 92.0                    9.0                        9.0   

   review_scores_checkin  review_scores_communication  review_scores_location  \
0                    9.0                         10.0                    10.0   
1                   10.0                         10.0                     9.0   
2                   10.0                         10.0                     9.0   

  review_scores_value  
0                10.0  
1                10.0  
2                 9.0  

[3 rows x 34 columns]

In [416]:
url_geojson = 'https://maps.amsterdam.nl/open_geodata/geojson_lnglat.php?KAARTLAAG=WONINGWAARDE_2021&THEMA=woningwaarde'
response = requests.get(url_geojson)
geojson_data = json.loads(response.content)
gdf = gpd.GeoDataFrame.from_features(geojson_data['features'])
gdf.head(3)

geometry  SELECTIE      LABEL
0  POLYGON ((4.97196 52.29421, 4.97164 52.29436, ...      4793  4793-5477
1  POLYGON ((4.96598 52.30445, 4.96568 52.30435, ...      3423  3423-4108
2  POLYGON ((4.97119 52.29115, 4.97108 52.29122, ...      4793  4793-5477

A Pandas Profile Report was used to better understand the raw data and identify potential issues. The report can be found in the repository as 'AirBnBProfileReport.html'. The report was used to throughout the cleaning and feature engineering process to identify issues and potential solutions.

In [417]:
pandas_profiling.ProfileReport(data).to_file('ProfilingReports//RAWairbnb.html')

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

### 4. Data Cleaning 


Whilst the dataset was partially cleaned and information was added, there were few issues that needed to be addressed. Individual columns were inspected for missing values, unique values and the number thereof, data types, and measures of central tendency. This was an iterative process that involved the above Profile Report to inspect variables.
Each and every column was inspected and cleaned as fit my purposes. Below is the code i thought was nessesary to clean the data. The main changes are discussed below afterwards as well as in the comments.




In [418]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7833 entries, 0 to 7832
Data columns (total 34 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   df_index                     7833 non-null   int64  
 1   host_id                      7833 non-null   int64  
 2   host_name                    7833 non-null   object 
 3   host_since_year              7833 non-null   int64  
 4   host_since_anniversary       7833 non-null   object 
 5   id                           7833 non-null   int64  
 6   neighbourhood_cleansed       7833 non-null   object 
 7   city                         7833 non-null   object 
 8   state                        7825 non-null   object 
 9   zipcode                      7660 non-null   object 
 10  country                      7833 non-null   object 
 11  latitude                     7833 non-null   float64
 12  longitude                    7833 non-null   float64
 13  property_type     

In [419]:
data.nunique()

df_index                       7833
host_id                        6378
host_name                      2987
host_since_year                   8
host_since_anniversary          366
id                             7813
neighbourhood_cleansed           22
city                             35
state                            22
zipcode                        3275
country                           1
latitude                       7810
longitude                      7813
property_type                    15
room_type                         3
accommodates                     14
bathrooms                        12
bedrooms                         11
beds                             14
bed_type                          5
price                           283
guests_included                  13
extra_people                     74
minimum_nights                   22
host_response_time                4
host_response_rate               85
number_of_reviews               186
review_scores_rating        

In [420]:
data.drop_duplicates(subset='id', keep='first', inplace=True) # This way each separate listing id is unique. A host can have multiple listings, but each listing has a unique id.
# Dropped 20 rows.
data.reset_index(drop=True, inplace=True)
data.shape

(7813, 34)

To handle missing values in the columns: **_'bathrooms'_**, **_'bedrooms'_** and **_'beds'_** i used a group-by with the **_'accomodates'_** variable. The assumption here is that a listing has a similar number of bathrooms, bedrooms and beds as other listings that accomodate the same number of people. 

In [421]:
mean_bathrooms = data.groupby('accommodates')['bathrooms'].transform('mean')
data['bathrooms_filled'] = data['bathrooms'].fillna(mean_bathrooms).apply(lambda x: round(x * 2) / 2) # Rounding to the nearest 0.5. Which represents a toilet. 

In [422]:
mean_bedrooms = data.groupby('accommodates')['bedrooms'].transform('mean')
data['bedrooms_filled'] = data['bedrooms'].fillna(mean_bedrooms).round() # using the float mean as an int (eg we cannot have 0.98 rooms).

In [423]:
mean_beds = data.groupby('accommodates')['beds'].transform('mean')
data['beds_filled'] = data['beds'].fillna(mean_beds).round()

In [424]:
# Transformations conducted above
data[['accommodates','beds', 'beds_filled','bathrooms','bathrooms_filled','bedrooms','bedrooms_filled']].iloc[[511,345,4712,7570]]

accommodates  beds  beds_filled  bathrooms  bathrooms_filled  bedrooms  \
511              2   NaN          1.0        NaN               1.0       1.0   
345              6   2.0          2.0        1.5               1.5       2.0   
4712             2   2.0          2.0        1.0               1.0       1.0   
7570             2   NaN          1.0        NaN               1.0       NaN   

      bedrooms_filled  
511               1.0  
345               2.0  
4712              1.0  
7570              1.0

I checked the correctness of the **_latitude_** and **_longitude_** columns. For this i used a bounding box of Amsterdam and checked if the coordinates were within this box.


In [425]:
amsterdam_bounds = {
    'lat_min': 52.2890,
    'lat_max': 52.4314,
    'lon_min': 4.7278,
    'lon_max': 5.0794
}

longs_in_box = data['longitude'].between(amsterdam_bounds['lon_min'], amsterdam_bounds['lon_max']).sum() # Summing the series of booleans.
lats_in_box = data['latitude'].between(amsterdam_bounds['lat_min'], amsterdam_bounds['lat_max']).sum()

longs_in_box, lats_in_box #And all are in bounds.

(7813, 7813)

### 5. Feature Engineering

**_Host Since Date_** column in datetime format (YYYY-MM-DD)

In [426]:
data['host_since'] = data['host_since_year'].astype(str) +'/'+ data['host_since_anniversary'].astype(str)
data['host_since'] = pd.to_datetime(data['host_since'], format='%Y/%m/%d')
data[['host_since_year', 'host_since_anniversary', 'host_since']].sample(3)


host_since_year host_since_anniversary host_since
2191             2012                  10/16 2012-10-16
1025             2012                   2/27 2012-02-27
3442             2013                   5/20 2013-05-20

**_'property_age'_** column is created using a timedelta shown in number of days.

In [427]:
current_date = dt.now()

data['host_since'] = pd.to_datetime(data['host_since'])
data['property_age'] = (current_date - data['host_since']).dt.days

**_'price_per_p'_**, **_'beds_per_p'_**, **_'bedrooms_per_p'_**, **_'bathrooms_per_p'_**, **_'num_of_rooms'_** columns are created by dividing the respective columns by the **_'accomodates'_** column. Except the latter which is created by adding the **_'bedrooms'_** and **_'bathrooms'_** columns as an indicator of the size of each listing.

In [428]:
data['price_per_p'] = data['price'] / data['accommodates']
data['beds_per_p'] = data['beds_filled'] / data['accommodates']
data['bedrooms_per_p'] = data['bedrooms_filled'] / data['accommodates']
data['bathrooms_per_p'] = data['bathrooms_filled'] / data['accommodates']
data['num_of_rooms'] = data['bedrooms_filled'] + data['bathrooms_filled']
data['rooms_per_p'] = data['num_of_rooms'] / data['accommodates']


At this point I add the data I downloaded earlier as a geojson. more specifically I am intrested in the Label column from the geo df, this shows me the minimum and maximum value per square foot of houses in a particular neighbourhood, this column was added as **_'label_price_ams'_**

In [429]:
data['label_price_ams'] = pd.Series(dtype='object') # create a new column to hold the labels from the geojson file

for i, row in data.iterrows(): # for each listing
    point = Point(row['longitude'], row['latitude']) #make a shapely point from the listing coordinates
    for j, poly in gdf.iterrows(): # for each polygon in the geojson file
        if point.within(poly.geometry): # check if the point is within the polygon
            data.loc[i, 'label_price_ams'] = poly['LABEL'] # if it is then assign the LABEL from the geojson to the listing
            break

Unfortunatley we still have 1000 listings that are not within the bounds of the geojson file. These listings are slightly off and seem to fall for example in a canal or in a park, its fair to assume the nearest polygon is the one we want to assign to these listings.

In [430]:
def nearest_poly(point, polygons): #passing a point and a gdf of polygons
    nearest_poly = None
    nearest_dist = float('inf') # set the nearest distance to infinity (very far away)
    for i, poly in polygons.iterrows(): # for each polygon in the geojson file
        dist = point.distance(poly.geometry) # calculate the distance between the point (listing) and the polygon's boundary
        if dist < nearest_dist: # if the distance is less than the nearest distance (which was very far away)
            nearest_poly = poly # then assign the polygon to the nearest_poly variable
            nearest_dist = dist # and assign the distance to the nearest_dist variable
    return nearest_poly # return the nearest polygon

In [431]:
%time
for i, row in data[data['label_price_ams'].isna()].iterrows(): # for each listing that is not exactly in a polygon and so is nan
    point = Point(row['longitude'], row['latitude']) # get the listings coordinates as a point
    nearest = nearest_poly(point, gdf) # gets the nearest polygon for that point #remember the return is a row of a the gdf
    data.loc[i, 'label_price_ams'] = nearest['LABEL'] # for that row of the gdf get the label and assign it to the corresponding row we are getting corrdinates from. 

Wall time: 0 ns


I then proceeded to treat the object data type extracted into numerical values **_'poly_min_price'_**, **_'poly_max_price'_**, **_'poly_mean_price'_** 

In [432]:
regex = re.compile(r'(\d+)') # regex to extract the min and max prices from the label_price_ams column it returns (in this case) a list with one or two numbers in it 

ls_min_max = data.label_price_ams.apply(lambda x: regex.findall(x)) # we make a list of lists eg 3420-1021 becomes ['3420', '1021'] (which is one row contained in a list of all the rows)

data['poly_min_price'] = [pair[0] for pair in ls_min_max] # we take the first number from each list and assign it to the min price column
data['poly_max_price'] = [pair[1] if len(pair) > 1 else pair[0] for pair in ls_min_max] # we take the second number from each list and assign it to the max price column, if there is no second number then we assign the first number to the max price column

data['poly_min_price'] = data['poly_min_price'].astype('float')
data['poly_max_price'] = data['poly_max_price'].astype('float')

data['poly_mean_price'] = data[['poly_min_price', 'poly_max_price']].mean(axis=1) # we take the mean along the row axis. 

**_'distance_to_dam_km'_** column is created using the **_latitude_** and **_longitude_** columns and the coordinates of the Dam Square in Amsterdam. This is done using the haversine formula under the hood of geodesic imported from geopy.distance.

In [433]:
# coordinates of dam square in amsterdam (generally considered the most central point of the city): 52.3731° N, 4.8922° E
dam_location = (52.3731, 4.8922)
data['distance_to_dam_km'] = data.apply(lambda x: geodesic(dam_location, (x['latitude'], x['longitude'])).km, axis=1)

##### Dropping irrelevant columns

- **_'index'_**: Unique identifier for each observation in the dataset (not needed and incorrect at this point).
- **_'host_since_year'_**, **_'host_since_anniversary'_**: have been dropped because they were turned into one column **_'host_since'_**
- **_'city'_**, **_'state'_**, **_'country'_**, **_'zipcode'_**: have been dropped given ill be working more closely with longitudes, latitudes and neighbourhoods more closely where possible. 
- **_'beds'_**, **_'bathrooms'_**, **_'bedrooms'_**: These are being dropped for their filled counter parts
- **_'label_price_ams'_**: This column is being dropped as it is was created whilst processing the geojson file and is not needed anymore.

In [434]:
data.drop(['df_index', 'host_since_year', 'host_since_anniversary', 'city', 'state', 'zipcode','country', 'bathrooms', 'beds', 'bedrooms', 'label_price_ams'], axis=1, inplace=True)

In [435]:
data.isna().sum()

host_id                           0
host_name                         0
id                                0
neighbourhood_cleansed            0
latitude                          0
longitude                         0
property_type                     0
room_type                         0
accommodates                      0
bed_type                          0
price                             0
guests_included                   0
extra_people                      0
minimum_nights                    0
host_response_time              730
host_response_rate              730
number_of_reviews                 0
review_scores_rating           1695
review_scores_accuracy         1706
review_scores_cleanliness      1706
review_scores_checkin          1705
review_scores_communication    1708
review_scores_location         1706
review_scores_value            1708
bathrooms_filled                  0
bedrooms_filled                   0
beds_filled                       0
host_since                  

In [436]:
data.dropna(inplace=True) # Finally i have decided to lazily drop the rows with missing valuse for the review columns (these were later added by the author). 
#Given the population of this analysis to be all AirBnB listings in Amsterdam, we will still have a large enough sample size to conduct the analysis and make valid conclusions. 

##### Handiling Outliers

Looking closer at the data i decided to exclude outliers, with that being said listings that are especially luxury or especially big are not really representative of the average listing (especially not the ones i am intrested in). To do so I considered two techniques to detect outliers by IQR or by z-score. i decided to use the latter as it made for more forgiving bound than the prior method. This means that all rows which contained values in any numerical feature where the value was in the bottom 2.5% and above 97.5% of the values in that feature were dropped.

In [437]:
# Make a mask that detects outliers outside of 3 standard deviations from the mean of numerical variables. 

numdata = data.select_dtypes(include=['int64', 'float64'])

numdata.drop(['host_id', 'id', 'latitude', 'longitude'], axis=1, inplace=True)


In [438]:
numdata_stats = numdata.describe().T

#Outlier bounds using Interquartile Range * 1.5 +/- the 75% and 25% quartiles
numdata_stats['IQR'] = numdata_stats['75%'] - numdata_stats['25%']
numdata_stats['IR_UB'] = (1.5 * numdata_stats['IQR']) + numdata_stats['75%']
numdata_stats['IR_LB'] = numdata_stats['25%'] - (1.5 * numdata_stats['IQR'])
numdata_stats['IR_LB'] = numdata_stats['IR_LB'].apply(lambda x: 0 if x < 0 else x)

#Outlier bounds using 3*Standard Deviation +/- the mean
numdata_stats['3sd_UB'] = numdata_stats['mean'] + (3 * numdata_stats['std'])
numdata_stats['3sd_LB'] = numdata_stats['mean'] - (3 * numdata_stats['std'])
numdata_stats['3sd_LB'] = numdata_stats['3sd_LB'].apply(lambda x: 0 if x < 0 else x) # LB not lower than 0 

# Looking at the bounds using the Standard deviation will result in less outliers being dropped in compared to the IQR method.

numdata_stats = numdata_stats[['std', 'mean', '3sd_UB', '3sd_LB']]
numdata_stats

std         mean        3sd_UB  \
accommodates                    1.744425     3.124298      8.357574   
price                          72.866443   124.060920    342.660249   
guests_included                 1.170951     1.696278      5.209130   
extra_people                   18.864982    14.491046     71.085992   
minimum_nights                  1.703972     2.457163      7.569079   
host_response_rate              0.147431     0.910544      1.352836   
number_of_reviews              28.317453    18.518434    103.470793   
review_scores_rating            7.379622    93.339361    115.478228   
review_scores_accuracy          0.801734     9.448034     11.853236   
review_scores_cleanliness       0.945332     9.296173     12.132170   
review_scores_checkin           0.716362     9.642381     11.791467   
review_scores_communication     0.633817     9.701896     11.603348   
review_scores_location          0.841488     9.300211     11.824674   
review_scores_value             0.861669     9.041081     11.626089   
bathrooms_filled                0.357834     1.104986      2.178489   
bedrooms_filled                 0.869797     1.397823      4.007214   
beds_filled                     1.648013     1.989115      6.933155   
property_age                  404.040541  3679.373771   4891.495394   
price_per_p                    18.423455    42.759724     98.030089   
beds_per_p                      0.231346     0.618643      1.312682   
bedrooms_per_p                  0.183928     0.468330      1.020114   
bathrooms_per_p                 0.174906     0.415094      0.939812   
num_of_rooms                    1.071701     2.502809      5.717913   
rooms_per_p                     0.294917     0.883424      1.768175   
poly_min_price               1075.299648  7560.159235  10786.058178   
poly_max_price               1444.500197  9230.869382  13564.369972   
poly_mean_price              1246.895888  8395.514308  12136.201973   
distance_to_dam_km              1.385725     2.239687      6.396861   

                                  3sd_LB  
accommodates                    0.000000  
price                           0.000000  
guests_included                 0.000000  
extra_people                    0.000000  
minimum_nights                  0.000000  
host_response_rate              0.468253  
number_of_reviews               0.000000  
review_scores_rating           71.200494  
review_scores_accuracy          7.042831  
review_scores_cleanliness       6.460175  
review_scores_checkin           7.493294  
review_scores_communication     7.800444  
review_scores_location          6.775747  
review_scores_value             6.456074  
bathrooms_filled                0.031483  
bedrooms_filled                 0.000000  
beds_filled                     0.000000  
property_age                 2467.252148  
price_per_p                     0.000000  
beds_per_p                      0.000000  
bedrooms_per_p                  0.000000  
bathrooms_per_p                 0.000000  
num_of_rooms                    0.000000  
rooms_per_p                     0.000000  
poly_min_price               4334.260291  
poly_max_price               4897.368792  
poly_mean_price              4654.826644  
distance_to_dam_km              0.000000

In [439]:


for i, row in numdata_stats.iterrows(): # loop through each row (col, bounds)
    upperbound = row['3sd_UB'] # assign the upper and lower bounds to variables
    lowerbound = row['3sd_LB']

    mask = (data[i] > upperbound) | (data[i] < lowerbound) # i here is the column name and so check if the data is outside the bounds with an or operator.
    data = data[~mask] # alternativley use .mask(mask) 

In [440]:
data.shape

(4473, 39)

##### Formatting the data before writing files
For further data analysis it might be useful to make a copy of the dataset with those categorical variables encoded to numbers. Lets also save a txt file with the dictionaries belonging to the encoded variables. 

In [441]:
column_dict = {
    'host_id': 'HostID',
    'host_name': 'HostName',
    'id': 'ID',
    'neighbourhood_cleansed': 'Neighbourhood',
    'latitude': 'Latitude',
    'longitude': 'Longitude',
    'property_type': 'PropertyType',
    'room_type': 'RoomType',
    'accommodates': 'Accommodates',
    'bed_type': 'BedType',
    'price': 'Price',
    'guests_included': 'GuestsIncluded',
    'extra_people': 'ExtraPeople',
    'minimum_nights': 'MinimumNights',
    'host_response_time': 'ResponseTime',
    'host_response_rate': 'ResponseRate',
    'number_of_reviews': 'NumberofReviews',
    'review_scores_rating': 'ReviewRating',
    'review_scores_accuracy': 'ReviewAccuracy',
    'review_scores_cleanliness': 'ReviewCleanliness',
    'review_scores_checkin': 'ReviewCheckin',
    'review_scores_communication': 'ReviewCommunication',
    'review_scores_location': 'ReviewLocation',
    'review_scores_value': 'ReviewValue',
    'bathrooms_filled': 'Bathrooms',
    'bedrooms_filled': 'Bedrooms',
    'beds_filled': 'Beds',
    'host_since': 'HostSince',
    'property_age': 'PropertyAge',
    'price_per_p': 'PriceperPerson',
    'beds_per_p': 'BedsperPerson',
    'bedrooms_per_p': 'BedroomsperPerson',
    'bathrooms_per_p': 'BathroomsperPerson',
    'num_of_rooms': 'NumberofRooms',
    'poly_min_price': 'PolyMinPrice',
    'poly_max_price': 'PolyMaxPrice',
    'poly_mean_price': 'PolyMeanPrice',
    'distance_to_dam_km': 'DistancetoDam(km)',
    'rooms_per_p':'RoomsperPerson'
}

data.rename(columns=column_dict, inplace=True)

In [442]:
dataencoded = data.copy()
dataencoded.drop('HostName', axis=1, inplace=True)

In [443]:
## Encoding categorical variables

dict_of_maps = {} # create a dictionary to store the maps
for col in dataencoded.select_dtypes('O').columns: # loop through each column that is of type object
    dict = {f'{col}':{}}
    for num, value in enumerate(dataencoded[col].unique()): # loop through each unique value in the column
        dict[f'{col}'].update({value: num}) # add the value and its corresponding number to the dictionary
    dict_of_maps.update(dict) # add the dictionary to the dictionary of maps
dict_of_maps

{'Neighbourhood': {'Centrum-Oost': 0,
  'Centrum-West': 1,
  'De Baarsjes - Oud-West': 2,
  'De Pijp - Rivierenbuurt': 3,
  'Oud-Oost': 4,
  'Westerpark': 5,
  'Oostelijk Havengebied - Indische Buurt': 6,
  'Bos en Lommer': 7,
  'Zuid': 8,
  'IJburg - Zeeburgereiland': 9,
  'Watergraafsmeer': 10,
  'Slotervaart': 11,
  'Buitenveldert - Zuidas': 12,
  'Geuzenveld - Slotermeer': 13,
  'Oud-Noord': 14,
  'Noord-West': 15,
  'Noord-Oost': 16,
  'Bijlmer-Centrum': 17},
 'PropertyType': {'Apartment': 0,
  'Boat': 1,
  'House': 2,
  'Bed & Breakfast': 3,
  'Loft': 4,
  'Villa': 5,
  'Cabin': 6,
  'Other': 7,
  'Chalet': 8,
  'Earth House': 9,
  'Camper/RV': 10,
  'Hut': 11,
  'Dorm': 12},
 'RoomType': {'Entire home/apt': 0, 'Private room': 1, 'Shared room': 2},
 'BedType': {'Real Bed': 0,
  'Pull-out Sofa': 1,
  'Futon': 2,
  'Couch': 3,
  'Airbed': 4},
 'ResponseTime': {'within an hour': 0,
  'within a few hours': 1,
  'within a day': 2,
  'a few days or more': 3}}

In [444]:
for key, value in dict_of_maps.items():
    dataencoded[key] = dataencoded[key].map(value) # map the values to the dataframe

Writing the two dataframes to csv files. Lets also save the maps we encoded our object columns with to a json file.

In [445]:
data.to_csv('Data/ClnListings.csv', index=False)
dataencoded.to_csv('Data/ClnListingsEncoded.csv', index=False)
with open('Data/EncodingMaps.json', 'w') as jfile:
    json.dump(dict_of_maps, jfile)

### 6. Data Analysis 


In [446]:
data = pd.read_csv('Data/ClnListings.csv')
dataencoded = pd.read_csv('Data/ClnListingsEncoded.csv')
with open('Data/EncodingMaps.json', 'r') as jfile:
    dict_of_maps = json.load(jfile)

In [447]:
data['HostSince'] = pd.to_datetime(data['HostSince'])

##### Research Questions

The following Research questions were used to guide the analysis of the data:

- **What are the correlations with AirBnB prices and the other features of the dataset? How much variance in price can be explained by other features?**
- **Which neighborhoods have significantly different prices amongst each other?**
- **Is there a correlation between AirBnB prices and housing values by neighborhood?**
- **What is the impact of reviews on the price of an AirBnB listings?**


In [448]:
data.describe().T

count          mean           std           min  \
HostID               4473.0  8.873020e+06  7.057204e+06  70937.000000   
ID                   4473.0  2.548532e+06  1.543148e+06  25488.000000   
Latitude             4473.0  5.236695e+01  1.305457e-02     52.319997   
Longitude            4473.0  4.887178e+00  2.547623e-02      4.807186   
Accommodates         4473.0  2.971160e+00  1.205726e+00      1.000000   
Price                4473.0  1.177114e+02  5.028918e+01     15.000000   
GuestsIncluded       4473.0  1.610329e+00  8.866687e-01      0.000000   
ExtraPeople          4473.0  1.345227e+01  1.635818e+01      0.000000   
MinimumNights        4473.0  2.378493e+00  1.188440e+00      1.000000   
ResponseRate         4473.0  9.233512e-01  1.212617e-01      0.470000   
NumberofReviews      4473.0  1.627476e+01  1.917064e+01      1.000000   
ReviewRating         4473.0  9.431545e+01  5.304163e+00     72.000000   
ReviewAccuracy       4473.0  9.551308e+00  6.082459e-01      8.000000   
ReviewCleanliness    4473.0  9.410686e+00  7.450746e-01      7.000000   
ReviewCheckin        4473.0  9.722334e+00  5.077967e-01      8.000000   
ReviewCommunication  4473.0  9.776884e+00  4.592835e-01      8.000000   
ReviewLocation       4473.0  9.379164e+00  6.967433e-01      7.000000   
ReviewValue          4473.0  9.147328e+00  6.757211e-01      7.000000   
Bathrooms            4473.0  1.069081e+00  2.201063e-01      0.500000   
Bedrooms             4473.0  1.322602e+00  6.676603e-01      0.000000   
Beds                 4473.0  1.800805e+00  1.098209e+00      1.000000   
PropertyAge          4473.0  3.674301e+03  3.899862e+02   2983.000000   
PriceperPerson       4473.0  4.220325e+01  1.577758e+01      6.333333   
BedsperPerson        4473.0  5.933673e-01  2.032368e-01      0.166667   
BedroomsperPerson    4473.0  4.565595e-01  1.638117e-01      0.000000   
BathroomsperPerson   4473.0  4.046843e-01  1.324982e-01      0.125000   
NumberofRooms        4473.0  2.391683e+00  7.646556e-01      0.500000   
RoomsperPerson       4473.0  8.612438e-01  2.316970e-01      0.142857   
PolyMinPrice         4473.0  7.665979e+03  9.133766e+02   4793.000000   
PolyMaxPrice         4473.0  9.368597e+03  1.245947e+03   5477.000000   
PolyMeanPrice        4473.0  8.517288e+03  1.064078e+03   5135.000000   
DistancetoDam(km)    4473.0  2.124913e+00  1.091104e+00      0.026597   

                              25%           50%           75%           max  
HostID               3.296959e+06  6.999042e+06  1.322135e+07  2.998796e+07  
ID                   1.181428e+06  2.452717e+06  3.871124e+06  5.780159e+06  
Latitude             5.235741e+01  5.236672e+01  5.237604e+01  5.242538e+01  
Longitude            4.869292e+00  4.886016e+00  4.901970e+00  4.983907e+00  
Accommodates         2.000000e+00  2.000000e+00  4.000000e+00  8.000000e+00  
Price                8.500000e+01  1.050000e+02  1.400000e+02  3.300000e+02  
GuestsIncluded       1.000000e+00  1.000000e+00  2.000000e+00  5.000000e+00  
ExtraPeople          0.000000e+00  0.000000e+00  2.500000e+01  7.000000e+01  
MinimumNights        2.000000e+00  2.000000e+00  3.000000e+00  7.000000e+00  
ResponseRate         9.000000e-01  1.000000e+00  1.000000e+00  1.000000e+00  
NumberofReviews      4.000000e+00  9.000000e+00  2.000000e+01  1.030000e+02  
ReviewRating         9.100000e+01  9.500000e+01  9.900000e+01  1.000000e+02  
ReviewAccuracy       9.000000e+00  1.000000e+01  1.000000e+01  1.000000e+01  
ReviewCleanliness    9.000000e+00  1.000000e+01  1.000000e+01  1.000000e+01  
ReviewCheckin        1.000000e+01  1.000000e+01  1.000000e+01  1.000000e+01  
ReviewCommunication  1.000000e+01  1.000000e+01  1.000000e+01  1.000000e+01  
ReviewLocation       9.000000e+00  9.000000e+00  1.000000e+01  1.000000e+01  
ReviewValue          9.000000e+00  9.000000e+00  1.000000e+01  1.000000e+01  
Bathrooms            1.000000e+00  1.000000e+00  1.000000e+00  2.000000e+00  
Bedrooms             1.000000e+00  1.000000e+00  2.0

In [449]:

hist_trace = go.Histogram(x=data['Price'], nbinsx=50, name='Price')

hist_layout = go.Layout(title='Price Distribution Bin:€19', xaxis_title='Price', yaxis_title='Count', template='plotly_dark', width=800)

fig = go.Figure(data=[hist_trace], layout=hist_layout)
print(f"Skewness: {stats.skew(data['Price'])}")
print(f"Kurtosis: {stats.kurtosis(data['Price'])}")
fig.show()

Skewness: 1.328634072298934
Kurtosis: 2.120106645225566


##### Linear Regression Analysis target variable: price

In [450]:
correlations = data.select_dtypes(include=['float64', 'int64'])
correlations.drop(['Latitude', 'Longitude','HostID','ID'], axis=1, inplace=True)

In [451]:

heatmap_data = go.Heatmap(z=correlations.corr(), x=correlations.columns, y=correlations.columns, colorscale='RdBu')
heatmap_layout = go.Layout(title='Heatmap of Numerical Variables in Data', template='plotly_dark', height=900, width=900)

fig = go.Figure(data=[heatmap_data], layout=heatmap_layout)
fig.show()

In [452]:

# Which are significantly correlated with price? How much of the price does each variable explain?
corr_var = [variab for variab in correlations.columns if variab != 'Price']
corr = data.corr()['Price']
results = {}

for var in corr_var:
    model = sm.OLS(data['Price'], sm.add_constant(data[var])).fit() # for each variable fit a linear regression model
    coef = model.params[var]
    r_squared = model.rsquared
    p_value = model.pvalues[var] #extract the statistics from the model
    
    if p_value < 0.05:
        significance = 'Significant'
    else:
        significance = 'Not significant' # determine if the variable is significant or not
    
    results[var] = {'Correlation': corr[var],'R-squared': r_squared, 'Coefficient': coef, 'P-Value': p_value,  'Significance': significance} 
    # add the statistics to the results dictionary

results_df = pd.DataFrame.from_dict(results, orient='index') # dictionary to a dataframe

results_df.sort_values(by='R-squared', ascending=False)

Correlation  R-squared  Coefficient        P-Value  \
NumberofRooms           0.539085   0.290612    35.454033   0.000000e+00   
Accommodates            0.534788   0.285998    22.305265   0.000000e+00   
Bedrooms                0.512476   0.262632    38.600483  3.758900e-298   
PriceperPerson          0.496249   0.246263     1.581736  8.037659e-277   
Beds                    0.480403   0.230787    21.998603  4.487143e-257   
GuestsIncluded          0.382722   0.146476    21.706830  5.321752e-156   
BathroomsperPerson     -0.375326   0.140870  -142.453537  1.232392e-149   
Bathrooms               0.318274   0.101298    72.718202  7.597984e-106   
DistancetoDam(km)      -0.293824   0.086332   -13.542391   8.905890e-90   
ReviewLocation          0.242784   0.058944    17.523531   5.096916e-61   
PolyMinPrice            0.171208   0.029312     0.009426   9.043163e-31   
PolyMeanPrice           0.167398   0.028022     0.007911   1.800802e-29   
BedsperPerson           0.163177   0.026627    40.376796   4.561554e-28   
RoomsperPerson         -0.162677   0.026464   -35.308684   6.650718e-28   
PolyMaxPrice            0.160418   0.025734     0.006475   3.603550e-27   
ExtraPeople             0.152147   0.023149     0.467738   1.418904e-24   
ReviewRating            0.150582   0.022675     1.427683   4.236427e-24   
MinimumNights           0.137862   0.019006     5.833661   2.007401e-20   
NumberofReviews        -0.097969   0.009598    -0.256997   5.161542e-11   
PropertyAge             0.091052   0.008290     0.011741   1.056989e-09   
BedroomsperPerson       0.073488   0.005400    22.560308   8.646394e-07   
ReviewAccuracy          0.073168   0.005354     6.049496   9.645287e-07   
ReviewCleanliness       0.068961   0.004756     4.654531   3.905902e-06   
ReviewCheckin           0.064243   0.004127     6.362229   1.709269e-05   
ReviewCommunication     0.055901   0.003125     6.120825   1.836266e-04   
ReviewValue             0.050144   0.002514     3.731898   7.940610e-04   
ResponseRate            0.016376   0.000268     6.791204   2.735289e-01   

                        Significance  
NumberofRooms            Significant  
Accommodates             Significant  
Bedrooms                 Significant  
PriceperPerson           Significant  
Beds                     Significant  
GuestsIncluded           Significant  
BathroomsperPerson       Significant  
Bathrooms                Significant  
DistancetoDam(km)        Significant  
ReviewLocation           Significant  
PolyMinPrice             Significant  
PolyMeanPrice            Significant  
BedsperPerson            Significant  
RoomsperPerson           Significant  
PolyMaxPrice             Significant  
ExtraPeople              Significant  
ReviewRating             Significant  
MinimumNights            Significant  
NumberofReviews          Significant  
PropertyAge              Significant  
BedroomsperPerson        Significant  
ReviewAccuracy           Significant  
ReviewCleanliness        Significant  
ReviewCheckin            Significant  
ReviewCommunication      Significant  
ReviewValue              Significant  
ResponseRate         Not significant

In [453]:
independent_vars = [var for var in correlations.columns if var != 'Price'] #list of independent variables

model = sm.OLS(data['Price'], sm.add_constant(correlations[independent_vars])) # this time fitting ols with all the variables
results = model.fit()

coef = results.params[independent_vars] # extract from the model using params dictionary 
p_values = results.pvalues[independent_vars] 

significance = ['Significant' if p < 0.05 else 'Not significant' for p in p_values] # determine significance

results_df = pd.DataFrame({'Coefficient': coef,
                           'P-Value': p_values,
                           'Significance': significance},
                          index=independent_vars) # create a dataframe of the results

overall_r_squared = results.rsquared
print(f"Overall R-squared: {overall_r_squared}") # print the overall r-squared for the multivariate model

constant = results.params['const']
print(f"Constant term: {constant}")

results_df.sort_values(by='P-Value', ascending=True)


Overall R-squared: 0.9147443110008185
Constant term: -38.762994437817824


Coefficient       P-Value     Significance
PriceperPerson       2.660287e+00  0.000000e+00      Significant
Accommodates         1.249964e+01  9.635810e-42      Significant
GuestsIncluded       2.150224e+00  5.402029e-11      Significant
ExtraPeople         -7.107340e-02  1.504042e-05      Significant
Beds                 3.429971e+00  2.076681e-04      Significant
ReviewLocation       1.115363e+00  4.535515e-03      Significant
DistancetoDam(km)   -6.163942e-01  2.035821e-02      Significant
BedsperPerson       -7.204424e+00  2.480109e-02      Significant
MinimumNights       -3.931681e-01  4.225275e-02      Significant
ReviewValue         -7.685961e-01  6.874496e-02  Not significant
ResponseRate         3.140732e+00  8.782345e-02  Not significant
ReviewCheckin        8.087234e-01  1.276569e-01  Not significant
ReviewRating        -8.427794e-02  1.655658e-01  Not significant
PropertyAge          3.230126e-04  5.919174e-01  Not significant
ReviewCommunication -1.276430e-01  8.273742e-01  Not significant
RoomsperPerson      -4.011529e+04  8.674298e-01  Not significant
BedroomsperPerson    4.007524e+04  8.675611e-01  Not significant
NumberofRooms        8.428418e+04  8.675763e-01  Not significant
Bedrooms            -8.426680e+04  8.676034e-01  Not significant
PolyMinPrice         5.720286e+08  8.676090e-01  Not significant
PolyMeanPrice       -1.144057e+09  8.676090e-01  Not significant
PolyMaxPrice         5.720286e+08  8.676090e-01  Not significant
Bathrooms           -8.423856e+04  8.676473e-01  Not significant
BathroomsperPerson   3.999124e+04  8.678361e-01  Not significant
NumberofReviews      1.010157e-03  9.352050e-01  Not significant
ReviewAccuracy      -1.376810e-02  9.760568e-01  Not significant
ReviewCleanliness   -1.033115e-02  9.777043e-01  Not significant

In [454]:
formula = 'Price = '

for i, row in results_df.iterrows(): 
    if row['Significance'] == 'Significant': # if the variable is significant
        formula += f" + {row['Coefficient']:.2f} * {i}" # add the coefficient and variable to the formula
formula += f" + {constant:.2f}" # add the constant to the formula

formula
        

'Price =  + 12.50 * Accommodates + 2.15 * GuestsIncluded + -0.07 * ExtraPeople + -0.39 * MinimumNights + 1.12 * ReviewLocation + 3.43 * Beds + 2.66 * PriceperPerson + -7.20 * BedsperPerson + -0.62 * DistancetoDam(km) + -38.76'

In [455]:
for col in correlations.columns:
    fig = go.Figure()
    trace1 = go.Scatter(x=data[f'{col}'], y=data['Price'], mode='markers')
                        
    fig.add_trace(trace1)
    fig.update_layout(title=f'{col} vs Price', template='plotly_dark', width=600, height=400)
    fig.show()

##### Statistical Analysis of Neighborhoods and Price

In [456]:
neigh_grpby = data.groupby('Neighbourhood')['Neighbourhood'].count().sort_values(ascending=False)

fig = go.Figure(
    data=[go.Bar(x=neigh_grpby.index, y=neigh_grpby.values)],
    layout=go.Layout(title='Number of Listings by Neighborhood', 
                     template='plotly_dark')
)

fig.show()

In [457]:
data.drop(data[data['Neighbourhood'] == 'Bijlmer-Centrum'].index, inplace=True)


In [458]:

neigh_price_grpby = data.groupby('Neighbourhood')['Price'].mean().sort_values(ascending=False)

fig = go.Figure(
    data=[go.Bar(x=neigh_price_grpby.index, y=neigh_price_grpby.values)],
    layout=go.Layout(title='Mean Price of Listings by Neighborhood', 
                     template='plotly_dark')
)

fig.show()

In [459]:
neigh_pricevalue_grpby = data.groupby('Neighbourhood')['PolyMeanPrice'].mean().sort_values(ascending=False)

fig = go.Figure(
    data=[go.Bar(x=neigh_pricevalue_grpby.index, y=neigh_pricevalue_grpby.values)],
    layout=go.Layout(title='Mean Price of Housing Values by m2 by Neighborhood', 
                     template='plotly_dark')
)

fig.show()

In [460]:
# Create an empty dictionary to store the neighborhood polygons
neighborhood_coordinates = {}

for neighbourhoods in data['Neighbourhood'].unique():
    neighborhood_coordinates.update({neighbourhoods: []}) # add each neighborhood to the dictionary

# Iterate over the listings in the DataFrame
for index, row in data.iterrows():
    # Extract the latitude, longitude, and neighborhood for each listing
    latitude = row['Longitude'] #yep not sure where i messed up but i did 
    longitude = row['Latitude']
    neighborhood = row['Neighbourhood']
    neighborhood_coordinates[neighborhood].append((latitude, longitude))

    

In [461]:
from scipy.spatial import ConvexHull

neighborhood_polygons = {}

# Compute the convex hull polygon for each neighborhood
for neighborhood, coordinates in neighborhood_coordinates.items():
    points = np.array(coordinates)
    
    hull = ConvexHull(points)

    hull_vertices = hull.vertices.tolist()

    # Create a polygon from the convex hull vertices
    polygon_coords = [(points[i, 0], points[i, 1]) for i in hull_vertices]
    polygon = Polygon(polygon_coords)

    # Store the polygon in the dictionary
    neighborhood_polygons[neighborhood] = polygon

neighborhood_polygons = gdf.from_dict(neighborhood_polygons, orient='index')
neighborhood_polygons


0
Centrum-Oost                            POLYGON ((4.907809183 52.3788838, 4.879396127 ...
Centrum-West                            POLYGON ((4.890020725 52.38832232, 4.884674494...
De Baarsjes - Oud-West                  POLYGON ((4.847086322 52.37149333, 4.849026629...
De Pijp - Rivierenbuurt                 POLYGON ((4.893596487 52.33761522, 4.901956885...
Oud-Oost                                POLYGON ((4.906166901 52.35732272, 4.907596489...
Westerpark                              POLYGON ((4.862031967 52.38286032, 4.865609412...
Oostelijk Havengebied - Indische Buurt  POLYGON ((4.954326749 52.37989755, 4.926990376...
Bos en Lommer                           POLYGON ((4.86385677 52.37543415, 4.862469644 ...
Zuid                                    POLYGON ((4.845089193 52.35235584, 4.845723405...
IJburg - Zeeburgereiland                POLYGON ((4.96051712 52.3812942, 4.958203326 5...
Watergraafsmeer                         POLYGON ((4.900958793 52.33303413, 4.905318351...
Slotervaart                             POLYGON ((4.840011817 52.37240631, 4.818858746...
Buitenveldert - Zuidas                  POLYGON ((4.889982304 52.32273909, 4.889752365...
Geuzenveld - Slotermeer                 POLYGON ((4.834793019 52.37306035, 4.838990099...
Oud-Noord                               POLYGON ((4.919604223 52.40029892, 4.886444589...
Noord-West                              POLYGON ((4.88990036 52.42538071, 4.878918671 ...
Noord-Oost                              POLYGON ((4.941492898 52.39735707, 4.945398676...

In [462]:
neigh_groupby = data.groupby('Neighbourhood').agg(PriceMean=('Price', 'mean'),
                                                  PriceStd=('Price', 'std'),
                                                  IDCount=('ID', 'count'),
                                                  PolyMeanPrice=('PolyMeanPrice', 'mean'))

neigh_df = pd.DataFrame(neigh_groupby).reset_index()
neigh_df

Neighbourhood   PriceMean   PriceStd  IDCount  \
0                            Bos en Lommer   91.472973  34.697225      222   
1                   Buitenveldert - Zuidas   96.350000  38.118943       40   
2                             Centrum-Oost  131.373383  48.969881      541   
3                             Centrum-West  143.236429  54.674284      829   
4                   De Baarsjes - Oud-West  111.069959  46.328252      729   
5                  De Pijp - Rivierenbuurt  119.285965  48.890006      570   
6                  Geuzenveld - Slotermeer   82.916667  41.725726       24   
7                 IJburg - Zeeburgereiland  103.652174  84.807058       23   
8                               Noord-Oost   89.000000  40.681691        5   
9                               Noord-West   99.676471  57.976338       34   
10  Oostelijk Havengebied - Indische Buurt  100.760000  46.708251      200   
11                               Oud-Noord   99.089286  42.705687      112   
12                                Oud-Oost  102.834783  33.137514      230   
13                             Slotervaart   90.012658  49.819030       79   
14                         Watergraafsmeer  103.640000  43.518374      100   
15                              Westerpark  109.619385  44.018461      423   
16                                    Zuid  117.562701  48.834167      311   

    PolyMeanPrice  
0     7573.092342  
1     7240.425000  
2     8727.342884  
3     8963.464415  
4     8918.073388  
5     8776.991228  
6     5619.937500  
7     5983.434783  
8     5271.900000  
9     6645.294118  
10    7433.882500  
11    7592.580357  
12    7992.860870  
13    6244.310127  
14    7630.725000  
15    8694.348700  
16    9103.225080

In [463]:

# Merge the DataFrames based on the 'Neighbourhood' column
merged_gdf = neighborhood_polygons.merge(neigh_df, left_on=neighborhood_polygons.index, right_on='Neighbourhood')
merged_gdf = gpd.GeoDataFrame(merged_gdf)
merged_gdf.set_geometry(0, inplace=True)

# Set the CRS of the GeoDataFrame
merged_gdf.crs = 'EPSG:4326'

# Reproject the GeoDataFrame to EPSG:4326
merged_gdf = merged_gdf.to_crs('EPSG:4326')

# Print the reprojected GeoDataFrame
merged_gdf

0  \
0   POLYGON ((4.90781 52.37888, 4.87940 52.36496, ...   
1   POLYGON ((4.89002 52.38832, 4.88467 52.38825, ...   
2   POLYGON ((4.84709 52.37149, 4.84903 52.35847, ...   
3   POLYGON ((4.89360 52.33762, 4.90196 52.33382, ...   
4   POLYGON ((4.90617 52.35732, 4.90760 52.35440, ...   
5   POLYGON ((4.86203 52.38286, 4.86561 52.37446, ...   
6   POLYGON ((4.95433 52.37990, 4.92699 52.38119, ...   
7   POLYGON ((4.86386 52.37543, 4.86247 52.38767, ...   
8   POLYGON ((4.84509 52.35236, 4.84572 52.34780, ...   
9   POLYGON ((4.96052 52.38129, 4.95820 52.36584, ...   
10  POLYGON ((4.90096 52.33303, 4.90532 52.32067, ...   
11  POLYGON ((4.84001 52.37241, 4.81886 52.35991, ...   
12  POLYGON ((4.88998 52.32274, 4.88975 52.33414, ...   
13  POLYGON ((4.83479 52.37306, 4.83899 52.38288, ...   
14  POLYGON ((4.91960 52.40030, 4.88644 52.40435, ...   
15  POLYGON ((4.88990 52.42538, 4.87892 52.41651, ...   
16  POLYGON ((4.94149 52.39736, 4.94540 52.39450, ...   

                             Neighbourhood   PriceMean   PriceStd  IDCount  \
0                             Centrum-Oost  131.373383  48.969881      541   
1                             Centrum-West  143.236429  54.674284      829   
2                   De Baarsjes - Oud-West  111.069959  46.328252      729   
3                  De Pijp - Rivierenbuurt  119.285965  48.890006      570   
4                                 Oud-Oost  102.834783  33.137514      230   
5                               Westerpark  109.619385  44.018461      423   
6   Oostelijk Havengebied - Indische Buurt  100.760000  46.708251      200   
7                            Bos en Lommer   91.472973  34.697225      222   
8                                     Zuid  117.562701  48.834167      311   
9                 IJburg - Zeeburgereiland  103.652174  84.807058       23   
10                         Watergraafsmeer  103.640000  43.518374      100   
11                             Slotervaart   90.012658  49.819030       79   
12                  Buitenveldert - Zuidas   96.350000  38.118943       40   
13                 Geuzenveld - Slotermeer   82.916667  41.725726       24   
14                               Oud-Noord   99.089286  42.705687      112   
15                              Noord-West   99.676471  57.976338       34   
16                              Noord-Oost   89.000000  40.681691        5   

    PolyMeanPrice  
0     8727.342884  
1     8963.464415  
2     8918.073388  
3     8776.991228  
4     7992.860870  
5     8694.348700  
6     7433.882500  
7     7573.092342  
8     9103.225080  
9     5983.434783  
10    7630.725000  
11    6244.310127  
12    7240.425000  
13    5619.937500  
14    7592.580357  
15    6645.294118  
16    5271.900000

In [464]:
merged_gdf.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [465]:
invalid_geometries = merged_gdf[~merged_gdf.geometry.is_valid]
print("Invalid geometries:", invalid_geometries)

Invalid geometries: Empty GeoDataFrame
Columns: [0, Neighbourhood, PriceMean, PriceStd, IDCount, PolyMeanPrice]
Index: []


In [466]:
merged_gdf.crs = 'EPSG:4326'

# Reverse the coordinates of the polygons
merged_gdf.geometry = merged_gdf.geometry.apply(lambda polygon: Polygon(polygon.exterior.coords[::-1]))

# Create a Folium map centered around Amsterdam
m = folium.Map(location=[52.3667, 4.8945], zoom_start=12)

# Define a color scale for the PriceMean values
color_scale = folium.LinearColormap(['green', 'yellow', 'red'], vmin=merged_gdf['PriceMean'].min(), vmax=merged_gdf['PriceMean'].max())

folium.GeoJson(
    merged_gdf,
    style_function=lambda feature: {
        'fillColor': color_scale(feature['properties']['PriceMean']),
        'color': 'black',
        'weight': 1,
        'fillOpacity': 0.6,
    },
    tooltip=folium.GeoJsonTooltip(
        fields=['Neighbourhood', 'PriceMean', 'PriceStd', 'IDCount', 'PolyMeanPrice'],
        aliases=['Neighbourhood', 'Price Mean', 'Price Std', 'ID Count', 'Poly Mean Price'],
        localize=True
    )
).add_to(m)

color_scale.add_to(m)

m


In [467]:
categorical_cols = [col for col in data.select_dtypes("O").columns if col != 'HostName']

In [472]:

fig = go.Figure()
trace1 = go.Box(x=data[f'Neighbourhood'], y=data['Price'])
                        
fig.add_trace(trace1)
fig.update_layout(title=f'Neighbourhood vs Price', template='plotly_dark', width=1500, height=600)
fig.show()
model = ols(f'Price ~ Neighbourhood', data=data).fit()

anova_table = sm.stats.anova_lm(model , typ=2)

propVarExp = (anova_table['sum_sq'][0] / (anova_table['sum_sq'][0] + anova_table['sum_sq'][1])) * 100
print(f'The proportion of variance explained by the Neighbourhood variable is {propVarExp:.2f}%')

anova_table


The proportion of variance explained by the Neighbourhood variable is 10.17%


sum_sq      df          F        PR(>F)
Neighbourhood  1.149862e+06    16.0  31.520762  1.132571e-91
Residual       1.015726e+07  4455.0        NaN           NaN

In [469]:
# Perform Tukey HSD test to perform pairwise comparisons
# the null hypothesis is that that two means are equal

tukey_results = pairwise_tukeyhsd(data['Price'], data['Neighbourhood'])

tukey_results_summary = tukey_results.summary()

tukey_df = pd.DataFrame(tukey_results_summary.data[1:], columns=tukey_results_summary.data[0])

In [470]:
tukey_df[tukey_df['reject'] == True].sort_values(by='meandiff', ascending=False) #.where((tukey_df['group1'] == 'Centrum-West') |(tukey_df['group2'] == 'Centrum-West')).dropna()

group1  \
2                             Bos en Lommer   
17                   Buitenveldert - Zuidas   
1                             Bos en Lommer   
16                   Buitenveldert - Zuidas   
4                             Bos en Lommer   
132                             Slotervaart   
15                            Bos en Lommer   
3                             Bos en Lommer   
125                               Oud-Noord   
14                            Bos en Lommer   
120  Oostelijk Havengebied - Indische Buurt   
129                                Oud-Oost   
31                             Centrum-Oost   
33                             Centrum-Oost   
44                             Centrum-Oost   
76                  De Pijp - Rivierenbuurt   
74                  De Pijp - Rivierenbuurt   
75                  De Pijp - Rivierenbuurt   
32                             Centrum-Oost   
66                   De Baarsjes - Oud-West   
43                             Centrum-Oost   
46                             Centrum-West   
57                             Centrum-West   
42                             Centrum-Oost   
40                             Centrum-Oost   
77                  De Pijp - Rivierenbuurt   
38                             Centrum-Oost   
37                             Centrum-Oost   
45                             Centrum-West   
39                             Centrum-Oost   
56                             Centrum-West   
70                  De Pijp - Rivierenbuurt   
48                             Centrum-West   
55                             Centrum-West   
53                             Centrum-West   
41                             Centrum-Oost   
51                             Centrum-West   
50                             Centrum-West   
52                             Centrum-West   
34                             Centrum-Oost   
54                             Centrum-West   
47                             Centrum-West   

                                     group2  meandiff   p-adj    lower  \
2                              Centrum-West   51.7635  0.0000  39.2768   
17                             Centrum-West   46.8864  0.0000  20.1379   
1                              Centrum-Oost   39.9004  0.0000  26.7304   
16                             Centrum-Oost   35.0234  0.0010   7.9491   
4                   De Pijp - Rivierenbuurt   27.8130  0.0000  14.7409   
132                                    Zuid   27.5500  0.0006   6.7322   
15                                     Zuid   26.0897  0.0000  11.5718   
3                    De Baarsjes - Oud-West   19.5970  0.0000   6.9307   
125                                    Zuid   18.4734  0.0425   0.2647   
14                               Westerpark   18.1464  0.0006   4.4524   
120                                    Zuid   16.8027  0.0114   1.8261   
129                                    Zuid   14.7279  0.0377   0.3581   
31                             Centrum-West   11.8630  0.0009   2.7307   
33                  De Pijp - Rivierenbuurt  -12.0874  0.0030 -22.0053   
44                                     Zuid  -13.8107  0.0056 -25.5688   
76                                 Oud-Oost  -16.4512  0.0013 -29.3587   
74   Oostelijk Havengebied - Indische Buurt  -18.5260  0.0003 -32.1057   
75                                Oud-Noord  -20.1967  0.0050 -37.2749   
32                   De Baarsjes - Oud-West  -20.3034  0.0000 -29.6799   
66                              Slotervaart  -21.0573  0.0205 -40.6289   
43                               Westerpark  -21.7540  0.0000 -32.4783   
46                  De Pijp - Rivierenbuurt  -23.9505  0.0000 -32.9411   
57                                     Zuid  -25.6737  0.0000 -36.6611   
42                          Watergraafsmeer  -27.7334  0.0000 -45.7191   
40                                 Oud-Oost  -28.5386  0.0000 -41.5452   
77                              Slotervaart  -29.2733  0.0000 -49.1100   
38   Oostelijk Ha

#### Extra Visualizations

In [186]:
fig1 = go.Figure()
trace1 = go.Violin(y=data['Accommodates'],
                          name='Accomodates')
trace2 = go.Violin(y=data['Bathrooms'],
                            name='Bathrooms')
trace3 = go.Violin(y=data['Bedrooms'],
                            name='Bedrooms')
trace4 = go.Violin(y=data['Beds'],
                            name='Beds')

trace_ls = [trace1, trace2, trace3, trace4]

for tra in trace_ls:
    fig1.add_trace(tra)

fig1.update_layout(title='Accomodation Violin Plots', showlegend=False, template='plotly_dark')

fig1.show()

In [188]:
fig2 = go.Figure()
#trace1 = go.Violin(y=data['number_of_reviews'],
#                          name='No. of Reviews')
trace2 = go.Violin(y=data['ReviewAccuracy'],
                            name='R. Accuracy')
trace3 = go.Violin(y=data['ReviewCheckin'],
                            name='R. Checkin')
trace4 = go.Violin(y=data['ReviewCleanliness'],
                            name='R. Cleanliness')
trace5 = go.Violin(y=data['ReviewCommunication'],
                            name='R. Communication')
trace6 = go.Violin(y=data['ReviewLocation'],
                            name='R. Location')
#trace7 = go.Violin(y=data['review_scores_rating'],
#                            name='R. Rating')
trace8 = go.Violin(y=data['ReviewValue'],
                            name='R. Value')
review_trace_ls = [ trace2, trace3, trace4, trace5, trace6, trace8]

for tra in review_trace_ls:
    fig2.add_trace(tra)

fig2.update_layout(title='Review Scores', showlegend=False, template='plotly_dark')

fig2.show()

In [190]:
fig = go.Figure()

trace1 = go.Pie(labels= data['RoomType'].value_counts().index, values= data.groupby('RoomType')['RoomType'].count())

fig.add_trace(trace1)

fig.update_layout(title='Room Types', template='plotly_dark', width=600, height=600)

fig

In [191]:
fig = go.Figure()

trace1 = go.Pie(labels= data['ResponseTime'].value_counts().index, values= data.groupby('ResponseTime')['ResponseTime'].count())

fig.add_trace(trace1)

fig.update_layout(title='Host response time', template='plotly_dark', width=600, height=600)

fig

In [211]:
prop_grpby = data.groupby('PropertyType')['PropertyType'].count()

fig = go.Figure(
    data=[go.Bar(x=prop_grpby.index, y=prop_grpby.values)],
    layout=go.Layout(title='Propery Type Count', 
                     template='plotly_dark')
)

fig.show()

In [201]:
review_cols = ['ReviewAccuracy', 'ReviewCheckin', 'ReviewCleanliness', 'ReviewCommunication', 'ReviewLocation', 'ReviewValue']

for var in review_cols:
    hist_trace = go.Histogram(x=data[f'{var}'], nbinsx=50, name=f'{var}')

    hist_layout = go.Layout(title=f'{var}', xaxis_title=f'{var}', yaxis_title='Count', template='plotly_dark', width=600, height=400)

    fig = go.Figure(data=[hist_trace], layout=hist_layout)
    print(f"Skewness: {stats.skew(data[f'{var}'])}")
    print(f"Kurtosis: {stats.kurtosis(data[f'{var}'])}")
    fig.show()

Skewness: -1.0135922671940427
Kurtosis: -0.005164295005678721


Skewness: -1.6288473634911738
Kurtosis: 1.7590341303972794


Skewness: -1.1038196188615468
Kurtosis: 0.6078666488229154


Skewness: -1.8949385280351105
Kurtosis: 2.7731657108244807


Skewness: -0.8312848003843252
Kurtosis: 0.0709771443627214


Skewness: -0.343429770625579
Kurtosis: -0.2297920669587481


## Conclusions

In an effort to better analyze the data the following questions were used to guide the analysis. Many of these questions were answred by looking at the linear regression statistical test for significance aswell as ANOVA tests when looking at data aggregated at a neighborhood level. The data cleaning and feature engineering process was described in detail in the relevant section of this notebook. Below are the insights and conclusions drawn from the analysis of data. 

The following 4 questions were ansred using Linear Regression Analysis:
- **What are the correlations with AirBnB prices and the other features of the dataset?** 
- **How much variance in price can be explained by other features? Which?**
- **Is there a correlation between AirBnB prices and housing values by neighborhood?**
- **What is the impact of reviews on the price of an AirBnB listings?**

I created a dataframe and fitted an Ordinary Least Squares Regression model to analyze the correlation between Price and each numerical independent variable. This allowed me to examine the R-squared values, coefficients, and significance of each variable by looking at their p-values. The DataFrame was then sorted in descending order based on the R-squared values. Although this analysis does not involve multiple linear regression, it provides insight into the individual variables that explain the most variance in Price and their relative importance in predicting it.

In descending order, the variables NumbeofRooms, Accommodates, Bedrooms, PriceperPerson, and Beds had R-squared values between 0.2 and 0.3. GuestsIncluded, BathroomperPerson, and Bathrooms individually explained between 0.1 and 0.14 of the variance in price. The next significant feature was DistancetoDam(km) at 0.086. While all the coefficients extracted were significant, the low R-squared values suggest that using any variable individually to explain changes in Price would not be advisable.

As a result, I conducted a multiple linear regression analysis to assess the combined effect of the independent variables on Price. The analysis revealed that the combined effect of the variables explains 91.48% of the variance in Price. Sorting the variables in ascending order according to their p-values, the significant coefficients were: PriceperPerson, BathroomsperPerson, Accommodates, BedroomsPerPerson, GuestsIncluded, ExtraPeople, Beds, ReviewLocation, DistancetoDam(km), BedsperPerson, and MinimumNights. The remaining variables' coefficients were not significant and were dropped from the regression model. The resulting formula from the Multiple Linear Regression Analysis is:

'Price = 12.50 * Accommodates + 2.15 * GuestsIncluded + (-0.07) * ExtraPeople + (-0.39) * MinimumNights + 1.12 * ReviewLocation + 3.43 * Beds + 2.66 * PriceperPerson + (-7.20) * BedsperPerson + (-0.62) * DistancetoDam(km) + (-38.76)'

The engineered features that were divided by the number of people a listing accommodates were more effective in explaining price than the variables themselves. Therefore, I was able to reduce the model to these 11 features. It is clear that the ratio between the size of a listing and the number of people it accommodates plays a significant role in predicting price. For example, an apartment with a high number of bedrooms or bathrooms per person tends to be more expensive due to its spaciousness. Contrary to expectations, the variables GuestsIncluded and ExtraPeople also have a significant impact on the price.

Furthermore, it is evident that independent variables related to location significantly impact price. Among all the review features, the location review is the only variable that significantly influences price prediction. The feature "Distance to Dam (km)," representing the distance between the listing and the central and touristic area of Amsterdam (Dam Square), also has a significant impact on predicting Price.

Finally, I found that the housing value per square meter in the neighborhood where the listing is located does not contribute significantly to price prediction beyond the variables already mentioned. Interestingly, neighborhoods around Prinsegracht and Vondel Park have higher prices compared to neighborhoods closer to Dam Square. This may be due to different preferences and needs between Amsterdam residents and tourists. Tourists prefer centrally located Airbnbs near famous landmarks, museums, and tourist activities, while residents opt for quieter and more livable areas further away from Dam Square. Although this hypothesis requires further research and investigation to be confirmed, it suggests opportunities for Airbnb hosts, as the most expensive neighborhoods in terms of price per night are not necessarily the most expensive neighborhoods per square meter in Amsterdam.

This leads me to the final research question explored in this project: 
**"Is there a difference in the Airbnb listings of Amsterdam among different neighborhoods regarding the price of the listing?"**
 To answer this question, I used ANOVA and Tukey's Honest Significant Difference (HSD) tests.

The ANOVA test was employed to identify significant differences in means between the neighborhood groups. It is important to note that the neighborhoods provided in the dataset do not overlap with the neighborhoods downloaded from Amsterdam's open map data. The latter offers more accurate segregation of neighborhoods compared to those given in the Airbnb dataset. Nonetheless, we used the downloaded neighborhoods to identify the most expensive neighborhoods.

The ANOVA test compares the distribution of prices among different neighborhoods with the distribution of prices within each neighborhood. The null hypothesis assumes no differences in listings across different neighborhoods regarding the price (i.e., they all have the same mean), while the alternative hypothesis (H1) suggests that at least two neighborhoods have different means.

With 16 degrees of freedom and an F-statistic of 31.52, the p-value is significant, indicating differences among at least two neighborhoods in terms of the mean price of Airbnb listings. The proportion of variance in price explained by the neighborhoods was calculated as the percentage of the sum of squares for the neighborhood factor out of the total sum of squares for the factor, including the residual sum of squares. The proportion of variance in price explained by neighborhoods is 10.17%. It is difficult to judge whether this value is high or not due to a lack of secondary research or similar tests on other variables like room type. However, including the neighborhood variable in the earlier created multiple linear regression model would likely enhance the R-squared value and contribute to better price prediction.

Finally, to visually explore the specific price differences, I created a map using folium and a new geopandas dataframe that outlines polygons for each neighborhood. Additionally, I conducted a Tukey HSD test after the ANOVA test to explore pairwise differences between different neighborhoods. Please refer to the relevant table for a breakdown of mean differences and their level of significance.

### Insights:
The most important factors influencing the variance in price for Airbnb listings are the spaciousness of the listing (in relation to the number of guests a Listing Accommodates), whether it allows extra services like additional guests, and the presence of a minimum number of nights. Location also plays a vital role in determining the price, particularly with respect to nearby touristic activities. Surprisingly, the per square meter housing values in different neighborhoods do not significantly affect the price prediction. This indicates that there are opportunities for Airbnb hosts to invest in listings outside of the most expensive areas of Amsterdam. In fact, areas that are more central but less expensive exhibit higher per-night prices than the expensive neighborhoods. This discrepancy arises from the distinct motivations and preferences when choosing a location for long-term living versus selecting a short-term stay as a tourist. Lastly, the most expensive neighborhoods in terms of price per night are those located close to the city center such as Centrum Eest, Centrum Oost, de Pijp and Zuid 

### My tip: 
Bos en Lommer offers more than 200 listings and has the third lowest mean price. The distribution of prices in this neighborhood is relatively small, ranging from 30 (lower fence) to 170 (upper fence), when compared to other neighborhoods like Westerpark, which is right next to Bos en Lommer. With excellent transportation connections, reaching Centrum West takes less than 10 minutes.

#### Further Research Recommendations:
- Incorporate more data about activities in Amsterdam, such as museums, healthcare facilities, sports venues, HORECA establishments (hotels/restaurants/cafes), parks, shopping areas, and coffee shops. By using geopandas, further analyze the correlation between these different functions surrounding a specific listing and their impact on the price of an Airbnb.

- Conduct further ANOVA analyses on categorical variables, such as room type, property type, and bed types available in different Airbnb listings.

- Use Machine Learning methods as opposed to statistical methods to predict Price. Then use SHAP values for further explanation of the impact and direction in which all independent variables affect Price. 

